In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt

In [2]:
train_dataset = pd.read_csv("train.csv")
test_dataset = pd.read_csv("test.csv")
train_dataset.head
train_dataset.describe()
train_dataset.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6500 entries, 0 to 6499
Data columns (total 20 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   Customer Id            6500 non-null   object 
 1   Artist Name            6500 non-null   object 
 2   Artist Reputation      5750 non-null   float64
 3   Height                 6125 non-null   float64
 4   Width                  5916 non-null   float64
 5   Weight                 5913 non-null   float64
 6   Material               5736 non-null   object 
 7   Price Of Sculpture     6500 non-null   float64
 8   Base Shipping Price    6500 non-null   float64
 9   International          6500 non-null   object 
 10  Express Shipment       6500 non-null   object 
 11  Installation Included  6500 non-null   object 
 12  Transport              5108 non-null   object 
 13  Fragile                6500 non-null   object 
 14  Customer Information   6500 non-null   object 
 15  Remo

In [3]:
import pandas_profiling
train_dataset.profile_report()

In [4]:
all_cols = list(train_dataset.columns)
num_cols = list(train_dataset._get_numeric_data().columns)
cat_cols = list(set(all_cols) - set(num_cols))


for i in cat_cols:
    train_dataset[i].fillna(train_dataset[i].mode()[0], inplace=True)
    test_dataset[i].fillna(test_dataset[i].mode()[0], inplace = True)
for i in cat_cols:    
    print(i,train_dataset[i].isnull().values.any())
    

Remote Location False
Transport False
Scheduled Date False
Fragile False
International False
Customer Location False
Installation Included False
Material False
Customer Id False
Express Shipment False
Customer Information False
Artist Name False
Delivery Date False


In [5]:
for i in num_cols:
    train_dataset[i].fillna(train_dataset[i].mode()[0], inplace = True)
    if i in test_dataset.columns:
        test_dataset[i].fillna(test_dataset[i].mode()[0], inplace = True)
for i in num_cols:
    print(i, train_dataset[i].isnull().values.any())

Artist Reputation False
Height False
Width False
Weight False
Price Of Sculpture False
Base Shipping Price False
Cost False


In [6]:
train_X = train_dataset
train_X.shape
train_X = train_X.drop(['Customer Id','Artist Name', 'Scheduled Date', 'Delivery Date', 'Customer Location'], axis = 1)
test_X = test_dataset
test_X = test_X.drop(['Artist Name','Customer Id', 'Scheduled Date', 'Delivery Date', 'Customer Location'], axis = 1)

In [7]:
from sklearn.preprocessing import OneHotEncoder
enc = OneHotEncoder(handle_unknown='ignore')
drop_list = ['Customer Id','Artist Name', 'Scheduled Date', 'Delivery Date', 'Customer Location']
for i in drop_list:
    if i in cat_cols:
        cat_cols.remove(i)
train_X = pd.get_dummies(train_X, columns = cat_cols)
test_X = pd.get_dummies(test_X, columns = cat_cols)

In [8]:
train_Y = train_X['Cost'].abs()
train_X = train_X.drop(['Cost'], axis=1)
train_X.shape

(6500, 28)

In [9]:
import sklearn
scaler = sklearn.preprocessing.StandardScaler()
train_X = pd.DataFrame(scaler.fit_transform(train_X), columns=train_X.columns)
test_X = pd.DataFrame(scaler.transform(test_X), columns=test_X.columns)

In [10]:
from sklearn.ensemble import RandomForestRegressor
rf = RandomForestRegressor(n_estimators=300)
rf.fit(train_X, train_Y)

RandomForestRegressor(n_estimators=300)

In [11]:
y_prediction_rf = rf.predict(test_X)

In [12]:
# Number of trees in random forest
n_estimators = [50,100,150,200,300,400,500]
# Maximum number of levels in tree
max_depth = [10,20,30,40,50,60,70]
max_depth.append(None)
# Method of selecting samples for training each tree
bootstrap = [True, False]

random_grid = {'n_estimators': n_estimators,
               'max_depth': max_depth,
               'bootstrap': bootstrap}

In [13]:
from sklearn.model_selection import RandomizedSearchCV
random_search_forest = RandomizedSearchCV(estimator = rf, param_distributions = random_grid, n_iter = 20,cv = 3)
random_search_forest.fit(train_X, train_Y)

RandomizedSearchCV(cv=3, estimator=RandomForestRegressor(n_estimators=300),
                   n_iter=20,
                   param_distributions={'bootstrap': [True, False],
                                        'max_depth': [10, 20, 30, 40, 50, 60,
                                                      70, None],
                                        'n_estimators': [50, 100, 150, 200, 300,
                                                         400, 500]})

In [14]:
tuned_best_rf = random_search_forest.best_estimator_
tuned_best_rf

RandomForestRegressor(max_depth=40, n_estimators=50)

In [15]:
tuned_best_rf.fit(train_X, train_Y)

RandomForestRegressor(max_depth=40, n_estimators=50)

In [16]:
tuned_rf_random_pred = tuned_best_rf.predict(test_X)

In [17]:
df = pd.DataFrame()
df['Customer Id'] = test_dataset['Customer Id']
df['Cost'] = y_prediction_rf
df['Cost'] = df['Cost'].abs()

In [18]:
df.to_csv('prediction6.csv', index = False)
df

Customer Id           Cost
0     fffe3400310033003300     234.321267
1     fffe3600350035003400     280.048000
2     fffe3700360030003500     219.432767
3         fffe350038003600     207.521567
4     fffe3500390032003500     334.068200
...                    ...            ...
3495  fffe3200300037003100    1342.885933
3496      fffe390031003100    2925.839000
3497  fffe3200350031003700    1030.865800
3498  fffe3100380031003000     183.347933
3499  fffe3200340037003300  166121.045533

[3500 rows x 2 columns]